In [7]:
!pip install torch

import torch
import numpy as np
import matplotlib.pyplot as plt
import torch.nn.functional as F

  Using cached torch-2.5.1-cp312-cp312-win_amd64.whl.metadata (28 kB)
Using cached torch-2.5.1-cp312-cp312-win_amd64.whl (203.0 MB)


In [25]:
words = open('names.txt', 'r').read().splitlines()

In [27]:
# names
## let's take 3 characters paris from the dataset
b = {}
for w in words[:10]:
  chs = ['.'] + list(w) + ['.']

  for ch1, ch2, ch3 in zip(chs,chs[1:], chs[2:]):
    # print(f'{ch1 = } {ch2 = } {ch3 = }')
    trigram = (ch1, ch2, ch3)
    b[trigram] = b.get(trigram, 0) + 1

In [29]:
sorted(b.items(), key = lambda kv: kv[1], reverse = True)

[(('i', 'a', '.'), 4),
 (('h', 'a', 'r'), 2),
 (('.', 'e', 'm'), 1),
 (('e', 'm', 'm'), 1),
 (('m', 'm', 'a'), 1),
 (('m', 'a', '.'), 1),
 (('.', 'o', 'l'), 1),
 (('o', 'l', 'i'), 1),
 (('l', 'i', 'v'), 1),
 (('i', 'v', 'i'), 1),
 (('v', 'i', 'a'), 1),
 (('.', 'a', 'v'), 1),
 (('a', 'v', 'a'), 1),
 (('v', 'a', '.'), 1),
 (('.', 'i', 's'), 1),
 (('i', 's', 'a'), 1),
 (('s', 'a', 'b'), 1),
 (('a', 'b', 'e'), 1),
 (('b', 'e', 'l'), 1),
 (('e', 'l', 'l'), 1),
 (('l', 'l', 'a'), 1),
 (('l', 'a', '.'), 1),
 (('.', 's', 'o'), 1),
 (('s', 'o', 'p'), 1),
 (('o', 'p', 'h'), 1),
 (('p', 'h', 'i'), 1),
 (('h', 'i', 'a'), 1),
 (('.', 'c', 'h'), 1),
 (('c', 'h', 'a'), 1),
 (('a', 'r', 'l'), 1),
 (('r', 'l', 'o'), 1),
 (('l', 'o', 't'), 1),
 (('o', 't', 't'), 1),
 (('t', 't', 'e'), 1),
 (('t', 'e', '.'), 1),
 (('.', 'm', 'i'), 1),
 (('m', 'i', 'a'), 1),
 (('.', 'a', 'm'), 1),
 (('a', 'm', 'e'), 1),
 (('m', 'e', 'l'), 1),
 (('e', 'l', 'i'), 1),
 (('l', 'i', 'a'), 1),
 (('.', 'h', 'a'), 1),
 (('a', 'r'

In [30]:
N = torch.zeros(27,27,27)
N.dtype
N

tensor([[[0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         ...,
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.]],

        [[0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         ...,
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.]],

        [[0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         ...,
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.]],

        ...,

        [[0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.],
         ...,
         [0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0., 

In [31]:
chars = sorted(list(set(''.join(words))))

stoi = {s:i+1 for i,s in enumerate(chars)}
stoi['.']  = 0
stoi

{'a': 1,
 'b': 2,
 'c': 3,
 'd': 4,
 'e': 5,
 'f': 6,
 'g': 7,
 'h': 8,
 'i': 9,
 'j': 10,
 'k': 11,
 'l': 12,
 'm': 13,
 'n': 14,
 'o': 15,
 'p': 16,
 'q': 17,
 'r': 18,
 's': 19,
 't': 20,
 'u': 21,
 'v': 22,
 'w': 23,
 'x': 24,
 'y': 25,
 'z': 26,
 '.': 0}

In [32]:
itos = {i:s for s,i in stoi.items()}
itos

{1: 'a',
 2: 'b',
 3: 'c',
 4: 'd',
 5: 'e',
 6: 'f',
 7: 'g',
 8: 'h',
 9: 'i',
 10: 'j',
 11: 'k',
 12: 'l',
 13: 'm',
 14: 'n',
 15: 'o',
 16: 'p',
 17: 'q',
 18: 'r',
 19: 's',
 20: 't',
 21: 'u',
 22: 'v',
 23: 'w',
 24: 'x',
 25: 'y',
 26: 'z',
 0: '.'}

In [33]:
for w in words:
  chs = ['.'] + list(w) + ['.']

  for ch1, ch2, ch3 in zip(chs, chs[1:], chs[2:]):
    ix1 = stoi[ch1]
    ix2 = stoi[ch2]
    ix3 = stoi[ch3]
    N[ix1, ix2, ix3] += 1

In [34]:
N

tensor([[[  0.,   0.,   0.,  ...,   0.,   0.,   0.],
         [  0., 207., 190.,  ...,  27., 173., 152.],
         [  0., 169.,   0.,  ...,   0.,   4.,   0.],
         ...,
         [  0.,  57.,   0.,  ...,   1.,  17.,  11.],
         [  0., 246.,   0.,  ...,   0.,   0.,   2.],
         [  0., 456.,   0.,  ...,   0.,  91.,   1.]],

        [[  0.,   0.,   0.,  ...,   0.,   0.,   0.],
         [ 40.,   0.,   5.,  ...,   0.,  20.,  11.],
         [ 36.,  28.,  20.,  ...,   0.,  12.,   0.],
         ...,
         [ 11.,   5.,   0.,  ...,  17.,   6.,   3.],
         [163., 389.,  13.,  ...,   0.,  16.,  40.],
         [ 38., 123.,   0.,  ...,   0.,  12.,  22.]],

        [[  0.,   0.,   0.,  ...,   0.,   0.,   0.],
         [ 46.,   5.,   5.,  ...,   4.,  31.,   4.],
         [  1.,   8.,   0.,  ...,   0.,   9.,   0.],
         ...,
         [  0.,   0.,   0.,  ...,   0.,   0.,   0.],
         [ 55.,   4.,   1.,  ...,   0.,   0.,   0.],
         [  0.,   0.,   0.,  ...,   0.,   0.,   0.]],

In [35]:
N.shape
type(N[2,3,1].item())
N[0,0]

tensor([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0.])

In [36]:
P = (N+1).float()
P /= torch.sum(P, dim = -1, keepdim = True)

In [37]:
g = torch.Generator().manual_seed(69)


for i in range(10):
  out = []
  ix1, ix2 = 0,0
  while True:

    p = P[ix1][ix2]

    ix1 = ix2

    ix2 = torch.multinomial(p, num_samples = 1,  replacement = True , generator = g).item()
    out.append(itos[ix2])
    if ix2 == 0:
      break

  print(''.join(out))

zaiyah.
krfjjwtzironslettheriaury.
ulakianovi.
jamarali.
vianova.
mariggugh.
buriany.
cora.
isqfynnalan.
lea.


In [ ]:
# from sre_constants import NOT_LITERAL
log_likelihood = 0.0
n = 0
nlls = []

for w in words:
  chs = ['.'] + list(w) + ['.']
  for ch1, ch2, ch3 in zip(chs, chs[1:], chs[2:]):
    ix1 = stoi[ch1]
    ix2 = stoi[ch2]
    ix3 = stoi[ch3]
    prob = P[ix1,ix2, ix3]
    n += 1
    logprob = torch.log(prob)
    # nlls[i] = nll
    log_likelihood += logprob
    print(f'{ch1}{ch2}{ch3} : {prob:.4f} {logprob:.4f}')

nll = -log_likelihood
print(nll)
print(f'average log likelihood : {nll/n:.4f}')

.em : 0.1855 -1.6847
emm : 0.1269 -2.0645
mma : 0.3744 -0.9825
ma. : 0.0669 -2.7050
.ol : 0.2494 -1.3887
oli : 0.1084 -2.2223
liv : 0.0219 -3.8195
ivi : 0.2669 -1.3209
via : 0.1578 -1.8465
ia. : 0.3657 -1.0060
.av : 0.0550 -2.9006
ava : 0.1882 -1.6705
va. : 0.1405 -1.9625
.is : 0.2023 -1.5982
isa : 0.1065 -2.2398
sab : 0.0627 -2.7693
abe : 0.3063 -1.1831
bel : 0.2962 -1.2168
ell : 0.2513 -1.3811
lla : 0.2464 -1.4010
la. : 0.2585 -1.3529
.so : 0.0735 -2.6106
sop : 0.0394 -3.2333
oph : 0.3115 -1.1664
phi : 0.2684 -1.3153
hia : 0.1085 -2.2213
ia. : 0.3657 -1.0060
.ch : 0.2250 -1.4917
cha : 0.3430 -1.0701
har : 0.1453 -1.9289
arl : 0.0875 -2.4360
rlo : 0.1023 -2.2801
lot : 0.0209 -3.8698
ott : 0.2414 -1.4214
tte : 0.3042 -1.1899
te. : 0.2369 -1.4402
.mi : 0.1536 -1.8734
mia : 0.0748 -2.5926
ia. : 0.3657 -1.0060
.am : 0.0868 -2.4445
ame : 0.1367 -1.9902
mel : 0.2237 -1.4976
eli : 0.1643 -1.8062
lia : 0.2070 -1.5749
ia. : 0.3657 -1.0060
.ha : 0.5616 -0.5770
har : 0.1453 -1.9289
arp : 0.0027 

In [39]:
#neural net sampling

#dataset creation
#since this is 2 input character + 1 output character
# we have 2 features

xs, ys = [], []

for w in words[:]:
  chs = ['.'] + list(w) + ['.']
  for ch1, ch2, ch3 in zip(chs, chs[1:], chs[2:]):
    ix1 = stoi[ch1]
    ix2 = stoi[ch2]
    ix2 = stoi[ch3]
    a = [ix1,ix2]
    xs.append(a)
    ys.append(ix3)

In [40]:
xs = torch.tensor(xs)
ys = torch.tensor(ys).reshape(196113,-1)

print(f'{xs.shape = }')
print(f'{ys.shape = }')

xs.shape = torch.Size([196113, 2])
ys.shape = torch.Size([196113, 1])


In [41]:
xenc = F.one_hot(xs, num_classes = 27).float()
# W = torch.random.randn(27, 196113)
output_size = 27  # example size
W = torch.nn.Parameter(torch.randn(27, output_size), requires_grad= True) * 0.01
# This would be applied to each of the 2 features separately

In [42]:
logits = xenc @ W
# logits
counts = logits.exp()

probs = counts / counts.sum(2, keepdim = True)
loss = -probs[torch.arange(probs.size(0)).view(-1, 1).expand(-1, 2), torch.arange(2).view(1, -1).expand(probs.size(0), -1), ys].log().mean() + 0.01 * W.mean()

W.grad = None
loss.backward()

W.grad

In [43]:
#  W.data += -10 * W.grad

In [60]:
# for i in range(100):
#   xenc = F.one_hot(xs, num_classes = 27).float()
#   logits = xenc @ W
#   counts = logits.exp()

#   probs = counts / counts.sum(2, keepdim = True)
#   loss = -probs[torch.arange(probs.size(0)).view(-1, 1).expand(-1, 2), torch.arange(2).view(1, -1).expand(probs.size(0), -1), ys].log().mean() + 0.01 * W.mean()

#   #backward pass
#   W.grad = None
#   loss.backward()


#   W.data += -1 * W.grad

#   if i % 100 == 0:
#     print(f' Epoch {i} :  loss {loss.item() }')
# forward pass
for i in range(100):
  xenc = F.one_hot(xs, num_classes = 27).float() # one-hot coded input character
  #linear
  logits = xenc @ W
  counts = logits.exp()
  #sigmoid
  probs = counts / counts.sum(2, keepdim = True)
  # loss = -probs[torch.arange(num),ys].log().mean() + 0.01 * W.mean()
  loss = -probs[torch.arange(probs.size(0)).view(-1, 1).expand(-1, 2), torch.arange(2).view(1, -1).expand(probs.size(0), -1), ys].log().mean() + 0.01 * W.mean()


  #backward pass
  W.grad = None
  loss.backward()

  W.data += -10 * W.grad
  if i % 10 == 0:
    print(f' loss : {loss.item() }')

RuntimeError: Trying to backward through the graph a second time (or directly access saved tensors after they have already been freed). Saved intermediate values of the graph are freed when you call .backward() or autograd.grad(). Specify retain_graph=True if you need to backward through the graph a second time or if you need to access saved tensors after calling backward.

In [ ]:
for i in range(20):

  out = []
  ix1, ix2 = 0, 0
  while True:
    xenc = F.one_hot(xs, num_classes = 27).float()
    logits = xenc @ W
    counts = logits.exp()
    # print(logits.shape)
    #sigmoid
    p = counts / counts.sum(1, keepdim = True)
    # print(p.shape)
    # ix1 = ix2
    # ix2 = torch.multinomial(p[ix1], num_samples = 1, replacement = True, generator = g).item()
    p = P[ix1][ix2]

    ix1 = ix2

    ix2 = torch.multinomial(p, num_samples = 1,  replacement = True , generator = g).item()
    out.append(itos[ix2])
    if ix2 == 0:
      break
  print(''.join(out))

In [ ]:
# 10 numbers

# lets say 5
y = 5
one_hot_coded = [0,0,0,0,0,0,1,0,0,0,0]

a2 = [0.01,0,0,0,0,0.5,0,0,0,0]

In [ ]:
# one_hot_encding

num_classes = 10
y = torch.tensor(y)
y

y_one_hot = F.one_hot(y, num_classes = 10)
y_one_hot